In [1]:
# Install required libraries

!pip install opencv-python
!pip install mediapipe
!pip install numpy
!pip install scikit-learn
!pip install matplotlib
!pip install kagglehub
!pip install tqdm

In [2]:
# Download and verify Kaggle dataset

import kagglehub
import os
import glob

KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
print("⏳ Downloading dataset from KaggleHub...")
try:
    dataset_path = kagglehub.dataset_download(KAGGLE_DATASET)
    print("✅ Dataset downloaded to:", dataset_path)
    print("📂 Dataset subdirectories:", [f.path for f in os.scandir(dataset_path) if f.is_dir()])
    image_paths = glob.glob(os.path.join(dataset_path, "**/*.*"), recursive=True)
    print("📷 Sample image paths (first 5):", image_paths[:5])
    if not image_paths:
        print("⚠️ Warning: No images found in dataset. Check dataset structure or download manually.")
except Exception as e:
    print(f"❌ Failed to download dataset: {e}")
    print("ℹ️ Try downloading manually from https://www.kaggle.com/datasets/abhishek14398/gesture-recognition-dataset")

⏳ Downloading dataset from KaggleHub...


100%|██████████| 1.60G/1.60G [00:18<00:00, 92.7MB/s]

Extracting files...


✅ Dataset downloaded to: /root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2
📂 Dataset subdirectories: ['/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/train', '/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/val']
📷 Sample image paths (first 5): ['/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/About-Dataset.txt', '/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/train.csv', '/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/val.csv', '/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/train/WIN_20180926_17_17_18_Pro_Thumbs_Down_new/WIN_20180926_17_17_18_Pro_00011.png', '/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/train/WIN_20180926_17_17_18_Pro_Thumbs_Down_new/WIN_20180926_17_17_18_Pro_00053.png']


In [3]:
# Gesture recognition program

import os
import cv2
import numpy as np
import mediapipe as mp
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
import matplotlib.pyplot as plt
from collections import deque
import kagglehub
import glob
from tqdm import tqdm

# ====== CONFIG ======
DATA_PATH = "gesture_data.npz"
GESTURE_LABELS = {0: 'wave', 1: 'stop', 2: 'thumbs_up'}
KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
USE_KAGGLEHUB = True
USE_REALTIME_COLLECTION = False
MAX_IMAGES_PER_CLASS = 1000  # Limit to prevent memory issues
AUGMENTATION_FACTOR = 2  # Number of augmented images per original image
MIN_DETECTION_CONFIDENCE = 0.5  # Lowered for better hand detection

# ====== MEDIAPIPE SETUP ======
mp_hands = mp.solutions.hands
mp_drawing = mp.solutions.drawing_utils
hands = mp_hands.Hands(max_num_hands=1, min_detection_confidence=MIN_DETECTION_CONFIDENCE)

def extract_features(landmarks):
    """Extract 3D coordinates from hand landmarks."""
    if not landmarks:
        return np.zeros(21 * 3)
    return np.array([coord for lm in landmarks for coord in (lm.x, lm.y, lm.z)])

def augment_image(image):
    """Apply random rotation and flip for data augmentation."""
    angle = np.random.uniform(-15, 15)
    h, w = image.shape[:2]
    M = cv2.getRotationMatrix2D((w/2, h/2), angle, 1)
    rotated = cv2.warpAffine(image, M, (w, h))
    if np.random.rand() > 0.5:
        rotated = cv2.flip(rotated, 1)  # Horizontal flip
    return rotated

def download_kagglehub_dataset():
    """Download and process Kaggle dataset with validation."""
    print("⏳ Downloading dataset from KaggleHub...")
    try:
        path = kagglehub.dataset_download(KAGGLE_DATASET)
        print("✅ Dataset downloaded to:", path)
        print("📂 Dataset contents:", [f.path for f in os.scandir(path) if f.is_dir()])
    except Exception as e:
        print(f"❌ Failed to download dataset: {e}")
        print("ℹ️ Try downloading manually from https://www.kaggle.com/datasets/abhishek14398/gesture-recognition-dataset")
        return None, None

    class_folders = [f.path for f in os.scandir(path) if f.is_dir()]
    if not class_folders:
        print("❌ No class folders found in dataset.")
        return None, None

    X, y = [], []
    for class_id, folder in enumerate(class_folders):
        print(f"📂 Processing folder: {os.path.basename(folder)} (Class ID: {class_id})")
        image_paths = glob.glob(os.path.join(folder, "*.*"))[:MAX_IMAGES_PER_CLASS]
        if not image_paths:
            print(f"⚠️ No images found in {folder}")
            continue
        print(f"📁 Found {len(image_paths)} images in {os.path.basename(folder)}")

        for image_path in tqdm(image_paths, desc=f"Processing {os.path.basename(folder)}"):
            img = cv2.imread(image_path)
            if img is None:
                print(f"❌ Failed to read: {image_path}")
                continue
            img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
            for _ in range(AUGMENTATION_FACTOR):
                aug_img = augment_image(img_rgb) if _ > 0 else img_rgb
                result = hands.process(aug_img)
                if result.multi_hand_landmarks:
                    for hand_landmarks in result.multi_hand_landmarks:
                        feature = extract_features(hand_landmarks.landmark)
                        X.append(feature)
                        y.append(class_id)
                else:
                    print(f"⚠️ No hand landmarks detected in {image_path}")

    X, y = np.array(X), np.array(y)
    print(f"✅ Extracted {len(X)} samples with {len(np.unique(y))} classes")
    if len(X) == 0:
        print("❌ No valid data extracted. Check dataset images or MediaPipe detection.")
        return None, None

    np.savez(DATA_PATH, X=X, y=y)
    print(f"✅ Saved dataset to {DATA_PATH}")
    return X, y

def collect_gesture_data():
    """Collect gesture data in real-time using webcam."""
    print("Press keys to label gestures: w (wave), s (stop), t (thumbs_up), q (quit)")
    key_to_label = {'w': 0, 's': 1, 't': 2}
    cap = cv2.VideoCapture(0)
    if not cap.isOpened():
        print("❌ Failed to open webcam.")
        return None, None
    data_X, data_y = [], []

    try:
        while True:
            ret, frame = cap.read()
            if not ret:
                print("❌ Failed to capture frame.")
                break
            rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            results = hands.process(rgb)

            label = None
            key = cv2.waitKey(1) & 0xFF
            if key == ord('q'):
                break
            elif chr(key) in key_to_label:
                label = key_to_label[chr(key)]

            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    mp_drawing.draw_landmarks(frame, hand_landmarks, mp_hands.HAND_CONNECTIONS)
                    features = extract_features(hand_landmarks.landmark)
                    if label is not None:
                        data_X.append(features)
                        data_y.append(label)
                        print(f"Collected: {GESTURE_LABELS[label]}")

            cv2.imshow("Collecting Gestures", frame)
    finally:
        cap.release()
        cv2.destroyAllWindows()

    data_X, data_y = np.array(data_X), np.array(data_y)
    if len(data_X) == 0:
        print("❌ No data collected.")
        return None, None
    np.savez(DATA_PATH, X=data_X, y=data_y)
    print(f"✅ Saved dataset to {DATA_PATH}")
    return data_X, data_y

def setup_live_plot():
    """Initialize live plot for gesture confidence."""
    plt.ion()
    fig, ax = plt.subplots(figsize=(8, 4))
    scores = deque(maxlen=30)
    line, = ax.plot(scores, color='#1f77b4')
    ax.set_ylim(0, 1)
    ax.set_title("Real-Time Gesture Confidence")
    ax.set_xlabel("Frames")
    ax.set_ylabel("Confidence")
    ax.grid(True)
    return fig, ax, line, scores

def train_and_run():
    """Train the model and run real-time gesture recognition."""
    # Load or collect data
    if os.path.exists(DATA_PATH):
        try:
            with np.load(DATA_PATH) as data:
                X, y = data['X'], data['y']
                print(f"✅ Loaded dataset from {DATA_PATH}: {len(X)} samples, {len(np.unique(y))} classes")
        except Exception as e:
            print(f"❌ Failed to load dataset from {DATA_PATH}: {e}")
            X, y = None, None
    elif USE_KAGGLEHUB:
        X, y = download_kagglehub_dataset()
    elif USE_REALTIME_COLLECTION:
        X, y = collect_gesture_data()
    else:
        print("⛔ No data source specified.")
        return

    if X is None or y is None or len(X) == 0:
        print("⛔ No valid data available. Check dataset or collection process.")
        return

    # Train model
    try:
        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
        classifier = SVC(kernel='linear', probability=True)
        classifier.fit(X_train, y_train)
        print(f"✅ Model trained. Test Accuracy: {accuracy_score(y_test, classifier.predict(X_test)):.2f}")
    except Exception as e:
        print(f"❌ Failed to train model: {e}")
        return

    # Setup real-time inference
    cap = cv2.VideoCapture(0)
    if not cap.isOpened():
        print("❌ Failed to open webcam.")
        return
    fig, ax, line, scores = setup_live_plot()

    try:
        while True:
            ret, frame = cap.read()
            if not ret:
                print("❌ Failed to capture frame.")
                break
            rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            results = hands.process(rgb)

            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    mp_drawing.draw_landmarks(frame, hand_landmarks, mp_hands.HAND_CONNECTIONS)
                    features = extract_features(hand_landmarks.landmark).reshape(1, -1)
                    probs = classifier.predict_proba(features)[0]
                    gesture_idx = np.argmax(probs)
                    gesture_name = GESTURE_LABELS.get(gesture_idx, "Unknown")
                    confidence = probs[gesture_idx]

                    scores.append(confidence)
                    line.set_ydata(scores)
                    line.set_xdata(np.arange(len(scores)))
                    ax.relim()
                    ax.autoscale_view()
                    fig.canvas.draw()
                    fig.canvas.flush_events()

                    cv2.putText(frame, f"{gesture_name} ({confidence:.2f})", (10, 30),
                                cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2)

            cv2.imshow("Real-Time Gesture Recognition", frame)
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
    finally:
        cap.release()
        cv2.destroyAllWindows()
        plt.close()

if __name__ == "__main__":
    train_and_run()

⏳ Downloading dataset from KaggleHub...
✅ Dataset downloaded to: /root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2
📂 Dataset contents: ['/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/train', '/root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/val']
📂 Processing folder: train (Class ID: 0)
⚠️ No images found in /root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/train
📂 Processing folder: val (Class ID: 1)
⚠️ No images found in /root/.cache/kagglehub/datasets/abhishek14398/gesture-recognition-dataset/versions/2/val
✅ Extracted 0 samples with 0 classes
❌ No valid data extracted. Check dataset images or MediaPipe detection.
⛔ No valid data available. Check dataset or collection process.


In [4]:
# Cell 3: Gesture recognition program
"""
Complete gesture recognition program with improved dataset handling and error checking.
"""
import os
import cv2
import numpy as np
import mediapipe as mp
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
import matplotlib.pyplot as plt
from collections import deque
import kagglehub
import glob
from tqdm import tqdm

# ====== CONFIG ======
DATA_PATH = "gesture_data.npz"
GESTURE_LABELS = {0: 'wave', 1: 'stop', 2: 'thumbs_up'}
KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
USE_KAGGLEHUB = True
USE_REALTIME_COLLECTION = False
MAX_IMAGES_PER_CLASS = 1000
AUGMENTATION_FACTOR = 2
MIN_DETECTION_CONFIDENCE = 0.5

# ====== MEDIAPIPE SETUP ======
mp_hands = mp.solutions.hands
mp_drawing = mp.solutions.drawing_utils
hands = mp_hands.Hands(max_num_hands=1, min_detection_confidence=MIN_DETECTION_CONFIDENCE)

def extract_features(landmarks):
    """Extract 3D coordinates from hand landmarks."""
    if not landmarks:
        return np.zeros(21 * 3)
    return np.array([coord for lm in landmarks for coord in (lm.x, lm.y, lm.z)])

def augment_image(image):
    """Apply random rotation and flip for data augmentation."""
    angle = np.random.uniform(-15, 15)
    h, w = image.shape[:2]
    M = cv2.getRotationMatrix2D((w/2, h/2), angle, 1)
    rotated = cv2.warpAffine(image, M, (w, h))
    if np.random.rand() > 0.5:
        rotated = cv2.flip(rotated, 1)
    return rotated

def download_kagglehub_dataset():
    """Download and process Kaggle dataset with recursive folder search."""
    print("⏳ Downloading dataset from KaggleHub...")
    try:
        path = kagglehub.dataset_download(KAGGLE_DATASET)
        print("✅ Dataset downloaded to:", path)
    except Exception as e:
        print(f"❌ Failed to download dataset: {e}")
        print("ℹ️ Try downloading manually from https://www.kaggle.com/datasets/abhishek14398/gesture-recognition-dataset")
        return None, None

    # Find all subdirectories recursively
    class_folders = []
    for root, dirs, _ in os.walk(path):
        for dir_name in dirs:
            if dir_name in GESTURE_LABELS.values():  # Only include folders matching gesture labels
                class_folders.append(os.path.join(root, dir_name))
    print("📂 Gesture folders found:", class_folders)
    if not class_folders:
        print("❌ No gesture folders (wave, stop, thumbs_up) found in dataset.")
        return None, None

    X, y = [], []
    for class_id, gesture in enumerate(GESTURE_LABELS.values()):
        # Find folder matching the gesture name
        matching_folders = [f for f in class_folders if gesture in os.path.basename(f)]
        for folder in matching_folders:
            print(f"📂 Processing folder: {os.path.basename(folder)} (Class ID: {class_id})")
            image_paths = glob.glob(os.path.join(folder, "*.*"))[:MAX_IMAGES_PER_CLASS]
            if not image_paths:
                print(f"⚠️ No images found in {folder}")
                continue
            print(f"📁 Found {len(image_paths)} images in {os.path.basename(folder)}")

            for image_path in tqdm(image_paths, desc=f"Processing {os.path.basename(folder)}"):
                img = cv2.imread(image_path)
                if img is None:
                    print(f"❌ Failed to read: {image_path}")
                    continue
                img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
                for _ in range(AUGMENTATION_FACTOR):
                    aug_img = augment_image(img_rgb) if _ > 0 else img_rgb
                    result = hands.process(aug_img)
                    if result.multi_hand_landmarks:
                        for hand_landmarks in result.multi_hand_landmarks:
                            feature = extract_features(hand_landmarks.landmark)
                            X.append(feature)
                            y.append(class_id)
                    else:
                        print(f"⚠️ No hand landmarks detected in {image_path}")

    X, y = np.array(X), np.array(y)
    print(f"✅ Extracted {len(X)} samples with {len(np.unique(y))} classes")
    if len(X) == 0:
        print("❌ No valid data extracted. Check dataset images or MediaPipe detection.")
        return None, None

    np.savez(DATA_PATH, X=X, y=y)
    print(f"✅ Saved dataset to {DATA_PATH}")
    return X, y

def collect_gesture_data():
    """Collect gesture data in real-time using webcam."""
    print("Press keys to label gestures: w (wave), s (stop), t (thumbs_up), q (quit)")
    key_to_label = {'w': 0, 's': 1, 't': 2}
    cap = cv2.VideoCapture(0)
    if not cap.isOpened():
        print("❌ Failed to open webcam. Falling back to dataset.")
        return None, None
    data_X, data_y = [], []

    try:
        while True:
            ret, frame = cap.read()
            if not ret:
                print("❌ Failed to capture frame.")
                break
            rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            results = hands.process(rgb)

            label = None
            key = cv2.waitKey(1) & 0xFF
            if key == ord('q'):
                break
            elif chr(key) in key_to_label:
                label = key_to_label[chr(key)]

            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    mp_drawing.draw_landmarks(frame, hand_landmarks, mp_hands.HAND_CONNECTIONS)
                    features = extract_features(hand_landmarks.landmark)
                    if label is not None:
                        data_X.append(features)
                        data_y.append(label)
                        print(f"Collected: {GESTURE_LABELS[label]}")

            cv2.imshow("Collecting Gestures", frame)
    finally:
        cap.release()
        cv2.destroyAllWindows()

    data_X, data_y = np.array(data_X), np.array(data_y)
    if len(data_X) == 0:
        print("❌ No data collected.")
        return None, None
    np.savez(DATA_PATH, X=data_X, y=data_y)
    print(f"✅ Saved dataset to {DATA_PATH}")
    return data_X, data_y

def setup_live_plot():
    """Initialize live plot for gesture confidence."""
    plt.ion()
    fig, ax = plt.subplots(figsize=(8, 4))
    scores = deque(maxlen=30)
    line, = ax.plot(scores, color='#1f77b4')
    ax.set_ylim(0, 1)
    ax.set_title("Real-Time Gesture Confidence")
    ax.set_xlabel("Frames")
    ax.set_ylabel("Confidence")
    ax.grid(True)
    return fig, ax, line, scores

def train_and_run():
    """Train the model and run real-time gesture recognition."""
    # Load or collect data
    if os.path.exists(DATA_PATH):
        try:
            with np.load(DATA_PATH) as data:
                X, y = data['X'], data['y']
                print(f"✅ Loaded dataset from {DATA_PATH}: {len(X)} samples, {len(np.unique(y))} classes")
        except Exception as e:
            print(f"❌ Failed to load dataset from {DATA_PATH}: {e}")
            X, y = None, None
    elif USE_KAGGLEHUB:
        X, y = download_kagglehub_dataset()
    elif USE_REALTIME_COLLECTION:
        X, y = collect_gesture_data()
    else:
        print("⛔ No data source specified.")
        return

    if X is None or y is None or len(X) == 0:
        print("⛔ No valid data available. Check dataset or collection process.")
        if not USE_REALTIME_COLLECTION:
            print("ℹ️ Trying real-time collection as fallback...")
            X, y = collect_gesture_data()
            if X is None or y is None or len(X) == 0:
                print("❌ Real-time collection failed. Exiting.")
                return

    # Train model
    try:
        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
        classifier = SVC(kernel='linear', probability=True)
        classifier.fit(X_train, y_train)
        print(f"✅ Model trained. Test Accuracy: {accuracy_score(y_test, classifier.predict(X_test)):.2f}")
    except Exception as e:
        print(f"❌ Failed to train model: {e}")
        return

    # Setup real-time inference
    cap = cv2.VideoCapture(0)
    if not cap.isOpened():
        print("❌ Failed to open webcam.")
        return
    fig, ax, line, scores = setup_live_plot()

    try:
        while True:
            ret, frame = cap.read()
            if not ret:
                print("❌ Failed to capture frame.")
                break
            rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            results = hands.process(rgb)

            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    mp_drawing.draw_landmarks(frame, hand_landmarks, mp_hands.HAND_CONNECTIONS)
                    features = extract_features(hand_landmarks.landmark).reshape(1, -1)
                    probs = classifier.predict_proba(features)[0]
                    gesture_idx = np.argmax(probs)
                    gesture_name = GESTURE_LABELS.get(gesture_idx, "Unknown")
                    confidence = probs[gesture_idx]

                    scores.append(confidence)
                    line.set_ydata(scores)
                    line.set_xdata(np.arange(len(scores)))
                    ax.relim()
                    ax.autoscale_view()
                    fig.canvas.draw()
                    fig.canvas.flush_events()

                    cv2.putText(frame, f"{gesture_name} ({confidence:.2f})", (10, 30),
                                cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2)

            cv2.imshow("Real-Time Gesture Recognition", frame)
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
    finally:
        cap.release()
        cv2.destroyAllWindows()
        plt.close()

if __name__ == "__main__":
    train_and_run()

⏳ Downloading dataset from KaggleHub...
✅ Dataset downloaded to: /kaggle/input/gesture-recognition-dataset
📂 Gesture folders found: []
❌ No gesture folders (wave, stop, thumbs_up) found in dataset.
⛔ No valid data available. Check dataset or collection process.
ℹ️ Trying real-time collection as fallback...
Press keys to label gestures: w (wave), s (stop), t (thumbs_up), q (quit)
❌ Failed to open webcam. Falling back to dataset.
❌ Real-time collection failed. Exiting.


In [6]:
!pip install opencv-python mediapipe numpy scikit-learn matplotlib kagglehub tqdm

In [7]:
import os
import glob
import kagglehub

KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
print("⏳ Downloading dataset from KaggleHub...")
try:
    dataset_path = kagglehub.dataset_download(KAGGLE_DATASET)
    print("✅ Dataset downloaded to:", dataset_path)
except Exception as e:
    print(f"❌ Failed to download dataset: {e}")
    dataset_path = "/kaggle/input/gesture-recognition-dataset"

print("📂 Dataset structure:")
for root, dirs, files in os.walk(dataset_path):
    print(f"Root: {root}, Dirs: {dirs}, Files: {len(files)}")
image_paths = glob.glob(os.path.join(dataset_path, "**/*.*"), recursive=True)
print(f"📷 Found {len(image_paths)} images. Sample paths (first 5):", image_paths[:5])
if not image_paths:
    print("⚠️ No images found. Please verify the dataset or add it via Kaggle 'Add Data'.")

⏳ Downloading dataset from KaggleHub...
✅ Dataset downloaded to: /kaggle/input/gesture-recognition-dataset
📂 Dataset structure:
Root: /kaggle/input/gesture-recognition-dataset, Dirs: ['val', 'train'], Files: 3
Root: /kaggle/input/gesture-recognition-dataset/val, Dirs: ['WIN_20180925_17_43_01_Pro_Left_Swipe_new', 'WIN_20180926_17_05_38_Pro_Thumbs_Down_new', 'WIN_20180907_16_07_10_Pro_Thumbs Down_new', 'WIN_20180925_17_47_07_Pro_Thumbs_Up_new', 'WIN_20180925_17_25_06_Pro_Right_Swipe_new', 'WIN_20180907_16_25_44_Pro_Stop Gesture_new', 'WIN_20180907_16_18_23_Pro_Thumbs Down_new', 'WIN_20180907_16_21_39_Pro_Left Swipe_new_Left Swipe_new', 'WIN_20180907_16_29_12_Pro_Thumbs Down_new', 'WIN_20180907_15_42_17_Pro_Stop Gesture_new', 'WIN_20180907_16_14_40_Pro_Right Swipe_new', 'WIN_20180907_15_38_42_Pro_Thumbs Up_new', 'WIN_20180907_16_10_59_Pro_Thumbs Up_new', 'WIN_20180926_17_28_32_Pro_Thumbs_Up_new', 'WIN_20180907_16_16_48_Pro_Stop Gesture_new', 'WIN_20180926_17_32_55_Pro_Left_Swipe_new', 'WI

In [8]:
import os
import cv2
import numpy as np
import mediapipe as mp
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
import kagglehub
import glob
from tqdm import tqdm

# ====== CONFIG ======
DATA_PATH = "gesture_data.npz"
KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
MAX_IMAGES_PER_CLASS = 1000
AUGMENTATION_FACTOR = 2
MIN_DETECTION_CONFIDENCE = 0.5

# ====== MEDIAPIPE SETUP ======
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(max_num_hands=1, min_detection_confidence=MIN_DETECTION_CONFIDENCE)

def extract_features(landmarks):
    """Extract 3D coordinates from hand landmarks."""
    if not landmarks:
        return np.zeros(21 * 3)
    return np.array([coord for lm in landmarks for coord in (lm.x, lm.y, lm.z)])

def augment_image(image):
    """Apply random rotation and flip for data augmentation."""
    angle = np.random.uniform(-15, 15)
    h, w = image.shape[:2]
    M = cv2.getRotationMatrix2D((w/2, h/2), angle, 1)
    rotated = cv2.warpAffine(image, M, (w, h))
    if np.random.rand() > 0.5:
        rotated = cv2.flip(rotated, 1)
    return rotated

def download_kagglehub_dataset():
    """Download and process Kaggle dataset with dynamic gesture labels."""
    print("⏳ Downloading dataset from KaggleHub...")
    try:
        path = kagglehub.dataset_download(KAGGLE_DATASET)
        print("✅ Dataset downloaded to:", path)
    except Exception as e:
        print(f"❌ Failed to download dataset: {e}")
        path = "/kaggle/input/gesture-recognition-dataset"
        if not os.path.exists(path):
            print("❌ Dataset path not found. Add it via Kaggle 'Add Data'.")
            return None, None, None

    # Find all directories with images
    image_dirs = []
    for root, dirs, files in os.walk(path):
        for dir_name in dirs:
            dir_path = os.path.join(root, dir_name)
            image_files = [f for f in os.listdir(dir_path) if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
            if image_files:
                image_dirs.append(dir_path)

    if not image_dirs:
        print("❌ No folders with images found.")
        return None, None, None

    # Create dynamic gesture labels based on folder names
    gesture_names = sorted(set(os.path.basename(d).lower() for d in image_dirs))
    GESTURE_LABELS = {i: name for i, name in enumerate(gesture_names)}
    print(f"📂 Detected gesture classes: {list(GESTURE_LABELS.values())}")

    X, y = [], []
    for class_id, gesture in enumerate(gesture_names):
        matching_dirs = [d for d in image_dirs if os.path.basename(d).lower() == gesture]
        for folder in matching_dirs:
            print(f"📂 Processing folder: {os.path.basename(folder)} (Class ID: {class_id})")
            image_paths = glob.glob(os.path.join(folder, "*.*"))[:MAX_IMAGES_PER_CLASS]
            if not image_paths:
                print(f"⚠️ No images found in {folder}")
                continue
            print(f"📁 Found {len(image_paths)} images")

            for image_path in tqdm(image_paths, desc=f"Processing {gesture}"):
                img = cv2.imread(image_path)
                if img is None:
                    print(f"❌ Failed to read: {image_path}")
                    continue
                img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
                for _ in range(AUGMENTATION_FACTOR):
                    aug_img = augment_image(img_rgb) if _ > 0 else img_rgb
                    result = hands.process(aug_img)
                    if result.multi_hand_landmarks:
                        for hand_landmarks in result.multi_hand_landmarks:
                            feature = extract_features(hand_landmarks.landmark)
                            X.append(feature)
                            y.append(class_id)
                    else:
                        print(f"⚠️ No hand landmarks detected in {image_path}")

    X, y = np.array(X), np.array(y)
    if len(X) == 0:
        print("❌ No valid data extracted. Check dataset images or MediaPipe detection.")
        return None, None, None

    print(f"✅ Extracted {len(X)} samples with {len(np.unique(y))} classes")
    np.savez(DATA_PATH, X=X, y=y)
    print(f"✅ Saved dataset to {DATA_PATH}")
    return X, y, GESTURE_LABELS

def train_and_run():
    """Train the model using the dataset."""
    # Load or process data
    if os.path.exists(DATA_PATH):
        try:
            with np.load(DATA_PATH) as data:
                X, y = data['X'], data['y']
                print(f"✅ Loaded dataset from {DATA_PATH}: {len(X)} samples, {len(np.unique(y))} classes")
        except Exception as e:
            print(f"❌ Failed to load dataset: {e}")
            X, y = None, None
    else:
        X, y, GESTURE_LABELS = download_kagglehub_dataset()

    if X is None or y is None or len(X) == 0:
        print("⛔ No valid data available. Exiting.")
        return

    # Train model
    try:
        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
        classifier = SVC(kernel='linear', probability=True)
        classifier.fit(X_train, y_train)
        print(f"✅ Model trained. Test Accuracy: {accuracy_score(y_test, classifier.predict(X_test)):.2f}")
    except Exception as e:
        print(f"❌ Failed to train model: {e}")

if __name__ == "__main__":
    train_and_run()

⏳ Downloading dataset from KaggleHub...
✅ Dataset downloaded to: /kaggle/input/gesture-recognition-dataset
📂 Detected gesture classes: ['win_20180907_15_30_06_pro_right swipe_new', 'win_20180907_15_35_09_pro_right swipe_new', 'win_20180907_15_38_17_pro_left swipe_new_left swipe_new', 'win_20180907_15_38_24_pro_right swipe_new', 'win_20180907_15_38_35_pro_thumbs down_new', 'win_20180907_15_38_42_pro_thumbs up_new', 'win_20180907_15_39_51_pro_stop gesture_new', 'win_20180907_15_39_54_pro_thumbs up_new', 'win_20180907_15_40_26_pro_thumbs down_new', 'win_20180907_15_40_55_pro_thumbs up_new', 'win_20180907_15_41_54_pro_right swipe_new', 'win_20180907_15_42_17_pro_stop gesture_new', 'win_20180907_15_42_25_pro_thumbs down_new', 'win_20180907_15_43_00_pro_left swipe_new_left swipe_new', 'win_20180907_15_43_28_pro_right swipe_new', 'win_20180907_15_43_36_pro_thumbs up_new', 'win_20180907_15_43_40_pro_stop gesture_new', 'win_20180907_15_43_58_pro_left swipe_new_left swipe_new', 'win_20180907_15_

Processing win_20180907_15_30_06_pro_right swipe_new:   3%|▎         | 1/30 [00:00<00:03,  9.61it/s]

⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/val/WIN_20180907_15_30_06_Pro_Right Swipe_new/WIN_20180907_15_30_06_Pro_00067.png
⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/val/WIN_20180907_15_30_06_Pro_Right Swipe_new/WIN_20180907_15_30_06_Pro_00067.png
⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/val/WIN_20180907_15_30_06_Pro_Right Swipe_new/WIN_20180907_15_30_06_Pro_00039.png
⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/val/WIN_20180907_15_30_06_Pro_Right Swipe_new/WIN_20180907_15_30_06_Pro_00039.png


Processing win_20180907_15_30_06_pro_right swipe_new:  10%|█         | 3/30 [00:00<00:01, 14.74it/s]

⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/val/WIN_20180907_15_30_06_Pro_Right Swipe_new/WIN_20180907_15_30_06_Pro_00047.png
⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/val/WIN_20180907_15_30_06_Pro_Right Swipe_new/WIN_20180907_15_30_06_Pro_00047.png


...

⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/train/WIN_20180926_18_09_50_Pro_Right_Swipe_new/WIN_20180926_18_09_50_Pro_00019.png
⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/train/WIN_20180926_18_09_50_Pro_Right_Swipe_new/WIN_20180926_18_09_50_Pro_00053.png
⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/train/WIN_20180926_18_09_50_Pro_Right_Swipe_new/WIN_20180926_18_09_50_Pro_00013.png


Processing win_20180926_18_09_50_pro_right_swipe_new:  97%|█████████▋| 29/30 [00:01<00:00, 14.72it/s]

⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/train/WIN_20180926_18_09_50_Pro_Right_Swipe_new/WIN_20180926_18_09_50_Pro_00029.png
⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/train/WIN_20180926_18_09_50_Pro_Right_Swipe_new/WIN_20180926_18_09_50_Pro_00069.png
⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/train/WIN_20180926_18_09_50_Pro_Right_Swipe_new/WIN_20180926_18_09_50_Pro_00039.png


Processing win_20180926_18_09_50_pro_right_swipe_new: 100%|██████████| 30/30 [00:01<00:00, 15.46it/s]


⚠️ No hand landmarks detected in /kaggle/input/gesture-recognition-dataset/train/WIN_20180926_18_09_50_Pro_Right_Swipe_new/WIN_20180926_18_09_50_Pro_00061.png
✅ Extracted 28180 samples with 755 classes
✅ Saved dataset to gesture_data.npz
✅ Model trained. Test Accuracy: 0.30


In [9]:
import os
import cv2
import numpy as np
import mediapipe as mp
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
import kagglehub
import glob
from tqdm import tqdm

# ====== CONFIG ======
DATA_PATH = "gesture_data.npz"
KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
MAX_IMAGES_PER_CLASS = 500  # Reduced to balance dataset
AUGMENTATION_FACTOR = 2
MIN_DETECTION_CONFIDENCE = 0.4  # Lowered to improve landmark detection
# Map dataset folder names to gesture labels
GESTURE_MAPPING = {
    '0': 'wave', '1': 'stop', '2': 'thumbs_up',  # Adjust based on actual folder names
    'wave': 'wave', 'stop': 'stop', 'thumbs_up': 'thumbs_up'
}
GESTURE_LABELS = {0: 'wave', 1: 'stop', 2: 'thumbs_up'}

# ====== MEDIAPIPE SETUP ======
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(max_num_hands=1, min_detection_confidence=MIN_DETECTION_CONFIDENCE)

def extract_features(landmarks):
    """Extract 3D coordinates from hand landmarks."""
    if not landmarks:
        return np.zeros(21 * 3)
    return np.array([coord for lm in landmarks for coord in (lm.x, lm.y, lm.z)])

def augment_image(image):
    """Apply random rotation and flip for data augmentation."""
    angle = np.random.uniform(-15, 15)
    h, w = image.shape[:2]
    M = cv2.getRotationMatrix2D((w/2, h/2), angle, 1)
    rotated = cv2.warpAffine(image, M, (w, h))
    if np.random.rand() > 0.5:
        rotated = cv2.flip(rotated, 1)
    return rotated

def download_kagglehub_dataset():
    """Download and process Kaggle dataset with mapped gesture labels."""
    print("⏳ Downloading dataset from KaggleHub...")
    try:
        path = kagglehub.dataset_download(KAGGLE_DATASET)
        print("✅ Dataset downloaded to:", path)
    except Exception as e:
        print(f"❌ Failed to download dataset: {e}")
        path = "/kaggle/input/gesture-recognition-dataset"
        if not os.path.exists(path):
            print("❌ Dataset path not found. Add via Kaggle 'Add Data'.")
            return None, None

    # Find directories with images
    image_dirs = []
    for root, dirs, files in os.walk(path):
        for dir_name in dirs:
            dir_path = os.path.join(root, dir_name)
            image_files = [f for f in os.listdir(dir_path) if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
            if image_files:
                image_dirs.append(dir_path)

    if not image_dirs:
        print("❌ No folders with images found.")
        return None, None

    # Filter and map directories to expected gestures
    valid_dirs = []
    for dir_path in image_dirs:
        folder_name = os.path.basename(dir_path).lower()
        if folder_name in GESTURE_MAPPING:
            valid_dirs.append((dir_path, GESTURE_MAPPING[folder_name]))
    print(f"📂 Valid gesture folders: {[f[0] for f in valid_dirs]}")

    if not valid_dirs:
        print("❌ No valid gesture folders found. Expected: wave, stop, thumbs_up or 0, 1, 2.")
        return None, None

    X, y = [], []
    for class_id, gesture in enumerate(GESTURE_LABELS.values()):
        matching_dirs = [d[0] for d in valid_dirs if d[1] == gesture]
        for folder in matching_dirs:
            print(f"📂 Processing folder: {os.path.basename(folder)} (Class ID: {class_id})")
            image_paths = glob.glob(os.path.join(folder, "*.*"))[:MAX_IMAGES_PER_CLASS]
            if not image_paths:
                print(f"⚠️ No images found in {folder}")
                continue
            print(f"📁 Found {len(image_paths)} images")

            for image_path in tqdm(image_paths, desc=f"Processing {gesture}"):
                img = cv2.imread(image_path)
                if img is None:
                    print(f"❌ Failed to read: {image_path}")
                    continue
                img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
                for _ in range(AUGMENTATION_FACTOR):
                    aug_img = augment_image(img_rgb) if _ > 0 else img_rgb
                    result = hands.process(aug_img)
                    if result.multi_hand_landmarks:
                        for hand_landmarks in result.multi_hand_landmarks:
                            feature = extract_features(hand_landmarks.landmark)
                            X.append(feature)
                            y.append(class_id)
                    else:
                        print(f"⚠️ No hand landmarks detected in {image_path}")

    X, y = np.array(X), np.array(y)
    if len(X) == 0:
        print("❌ No valid data extracted. Check dataset images or MediaPipe detection.")
        return None, None

    print(f"✅ Extracted {len(X)} samples with {len(np.unique(y))} classes")
    np.savez(DATA_PATH, X=X, y=y)
    print(f"✅ Saved dataset to {DATA_PATH}")
    return X, y

def train_and_run():
    """Train the model using the dataset."""
    # Load or process data
    if os.path.exists(DATA_PATH):
        try:
            with np.load(DATA_PATH) as data:
                X, y = data['X'], data['y']
                print(f"✅ Loaded dataset from {DATA_PATH}: {len(X)} samples, {len(np.unique(y))} classes")
        except Exception as e:
            print(f"❌ Failed to load dataset: {e}")
            X, y = None, None
    else:
        X, y = download_kagglehub_dataset()

    if X is None or y is None or len(X) == 0:
        print("⛔ No valid data available. Exiting.")
        return

    # Train model
    try:
        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
        classifier = SVC(kernel='rbf', probability=True)  # Switched to RBF kernel for better performance
        classifier.fit(X_train, y_train)
        print(f"✅ Model trained. Test Accuracy: {accuracy_score(y_test, classifier.predict(X_test)):.2f}")
    except Exception as e:
        print(f"❌ Failed to train model: {e}")

if __name__ == "__main__":
    train_and_run()

✅ Loaded dataset from gesture_data.npz: 28180 samples, 755 classes
✅ Model trained. Test Accuracy: 0.18


In [12]:
import os
import cv2
import numpy as np
import mediapipe as mp
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
import kagglehub
import glob
from tqdm import tqdm

# ====== CONFIG ======
DATA_PATH = "gesture_data.npz"
KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
MAX_IMAGES_PER_CLASS = 500
AUGMENTATION_FACTOR = 2
MIN_DETECTION_CONFIDENCE = 0.4
# Map dataset folder names to gesture labels
GESTURE_MAPPING = {
    '0': 'wave', '1': 'stop', '2': 'thumbs_up',
    'wave': 'wave', 'stop': 'stop', 'thumbs_up': 'thumbs_up'
}
GESTURE_LABELS = {0: 'wave', 1: 'stop', 2: 'thumbs_up'}

# ====== MEDIAPIPE SETUP ======
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(max_num_hands=1, min_detection_confidence=MIN_DETECTION_CONFIDENCE)

def extract_features(landmarks):
    """Extract 3D coordinates from hand landmarks."""
    if not landmarks:
        return np.zeros(21 * 3)
    return np.array([coord for lm in landmarks for coord in (lm.x, lm.y, lm.z)])

def augment_image(image):
    """Apply random rotation and flip for data augmentation."""
    angle = np.random.uniform(-15, 15)
    h, w = image.shape[:2]
    M = cv2.getRotationMatrix2D((w/2, h/2), angle, 1)
    rotated = cv2.warpAffine(image, M, (w, h))
    if np.random.rand() > 0.5:
        rotated = cv2.flip(rotated, 1)
    return rotated

def download_kagglehub_dataset():
    """Download and process Kaggle dataset with strict class filtering."""
    print("⏳ Downloading dataset from KaggleHub...")
    try:
        path = kagglehub.dataset_download(KAGGLE_DATASET)
        print("✅ Dataset downloaded to:", path)
    except Exception as e:
        print(f"❌ Failed to download dataset: {e}")
        path = "/kaggle/input/gesture-recognition-dataset"
        if not os.path.exists(path):
            print("❌ Dataset path not found. Add via Kaggle 'Add Data'.")
            return None, None

    # Find directories with images
    image_dirs = []
    for root, dirs, files in os.walk(path):
        for dir_name in dirs:
            dir_path = os.path.join(root, dir_name)
            image_files = [f for f in os.listdir(dir_path) if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
            if image_files:
                image_dirs.append(dir_path)

    if not image_dirs:
        print("❌ No folders with images found.")
        return None, None

    # Filter directories to only valid gestures
    valid_dirs = []
    for dir_path in image_dirs:
        folder_name = os.path.basename(dir_path).lower()
        if folder_name in GESTURE_MAPPING:
            valid_dirs.append((dir_path, GESTURE_MAPPING[folder_name]))
    print(f"📂 Valid gesture folders: {[f[0] for f in valid_dirs]}")

    if not valid_dirs:
        print("❌ No valid gesture folders found. Expected: wave, stop, thumbs_up or 0, 1, 2.")
        return None, None

    X, y = [], []
    for class_id, gesture in enumerate(GESTURE_LABELS.values()):
        matching_dirs = [d[0] for d in valid_dirs if d[1] == gesture]
        for folder in matching_dirs:
            print(f"📂 Processing folder: {os.path.basename(folder)} (Class ID: {class_id})")
            image_paths = glob.glob(os.path.join(folder, "*.*"))[:MAX_IMAGES_PER_CLASS]
            if not image_paths:
                print(f"⚠️ No images found in {folder}")
                continue
            print(f"📁 Found {len(image_paths)} images")

            for image_path in tqdm(image_paths, desc=f"Processing {gesture}"):
                img = cv2.imread(image_path)
                if img is None:
                    print(f"❌ Failed to read: {image_path}")
                    continue
                img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
                for _ in range(AUGMENTATION_FACTOR):
                    aug_img = augment_image(img_rgb) if _ > 0 else img_rgb
                    result = hands.process(aug_img)
                    if result.multi_hand_landmarks:
                        for hand_landmarks in result.multi_hand_landmarks:
                            feature = extract_features(hand_landmarks.landmark)
                            X.append(feature)
                            y.append(class_id)
                    else:
                        print(f"⚠️ No hand landmarks detected in {image_path}")

    X, y = np.array(X), np.array(y)
    if len(X) == 0:
        print("❌ No valid data extracted. Check dataset images or MediaPipe detection.")
        return None, None

    print(f"✅ Extracted {len(X)} samples with {len(np.unique(y))} classes")
    np.savez(DATA_PATH, X=X, y=y)
    print(f"✅ Saved dataset to {DATA_PATH}")
    return X, y

def train_and_run():
    """Train the model with feature scaling."""
    # Load or process data
    if os.path.exists(DATA_PATH):
        try:
            with np.load(DATA_PATH) as data:
                X, y = data['X'], data['y']
                print(f"✅ Loaded dataset from {DATA_PATH}: {len(X)} samples, {len(np.unique(y))} classes")
        except Exception as e:
            print(f"❌ Failed to load dataset: {e}")
            X, y = None, None
    else:
        X, y = download_kagglehub_dataset()

    if X is None or y is None or len(X) == 0:
        print("⛔ No valid data available. Exiting.")
        return

    # Train model with feature scaling
    try:
        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
        scaler = StandardScaler()
        X_train = scaler.fit_transform(X_train)
        X_test = scaler.transform(X_test)
        classifier = SVC(kernel='rbf', probability=True)
        classifier.fit(X_train, y_train)
        print(f"✅ Model trained. Test Accuracy: {accuracy_score(y_test, classifier.predict(X_test)):.2f}")
    except Exception as e:
        print(f"❌ Failed to train model: {e}")

if __name__ == "__main__":
    train_and_run()

✅ Loaded dataset from gesture_data.npz: 28180 samples, 755 classes
✅ Model trained. Test Accuracy: 0.41


In [15]:
import os
import glob
import kagglehub

KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
print("⏳ Downloading dataset from KaggleHub...")
try:
    dataset_path = kagglehub.dataset_download(KAGGLE_DATASET)
    print("✅ Dataset downloaded to:", dataset_path)
except Exception as e:
    print(f"❌ Failed to download dataset: {e}")
    dataset_path = "./gesture-recognition-dataset"  # Adjust to local path if manually downloaded

print("📂 Dataset structure:")
for root, dirs, files in os.walk(dataset_path):
    print(f"Root: {root}, Dirs: {dirs}, Files: {len(files)}")
image_paths = glob.glob(os.path.join(dataset_path, "**/*.*"), recursive=True)
print(f"📷 Found {len(image_paths)} images. Sample paths (first 5):", image_paths[:5])
if not image_paths:
    print("⚠️ No images found. Verify the dataset path or download from https://www.kaggle.com/datasets/abhishek14398/gesture-recognition-dataset")

⏳ Downloading dataset from KaggleHub...
✅ Dataset downloaded to: /kaggle/input/gesture-recognition-dataset
📂 Dataset structure:
Root: /kaggle/input/gesture-recognition-dataset, Dirs: ['val', 'train'], Files: 3
Root: /kaggle/input/gesture-recognition-dataset/val, Dirs: ['WIN_20180925_17_43_01_Pro_Left_Swipe_new', 'WIN_20180926_17_05_38_Pro_Thumbs_Down_new', 'WIN_20180907_16_07_10_Pro_Thumbs Down_new', 'WIN_20180925_17_47_07_Pro_Thumbs_Up_new', 'WIN_20180925_17_25_06_Pro_Right_Swipe_new', 'WIN_20180907_16_25_44_Pro_Stop Gesture_new', 'WIN_20180907_16_18_23_Pro_Thumbs Down_new', 'WIN_20180907_16_21_39_Pro_Left Swipe_new_Left Swipe_new', 'WIN_20180907_16_29_12_Pro_Thumbs Down_new', 'WIN_20180907_15_42_17_Pro_Stop Gesture_new', 'WIN_20180907_16_14_40_Pro_Right Swipe_new', 'WIN_20180907_15_38_42_Pro_Thumbs Up_new', 'WIN_20180907_16_10_59_Pro_Thumbs Up_new', 'WIN_20180926_17_28_32_Pro_Thumbs_Up_new', 'WIN_20180907_16_16_48_Pro_Stop Gesture_new', 'WIN_20180926_17_32_55_Pro_Left_Swipe_new', 'WI

In [16]:
import os
import cv2
import numpy as np
import mediapipe as mp
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
import matplotlib.pyplot as plt
from collections import deque
import kagglehub
import glob
from tqdm import tqdm

# ====== CONFIG ======
DATA_PATH = "gesture_data.npz"
KAGGLE_DATASET = "abhishek14398/gesture-recognition-dataset"
MAX_IMAGES_PER_CLASS = 500
AUGMENTATION_FACTOR = 3  # Increased for more varied data
MIN_DETECTION_CONFIDENCE = 0.3  # Lowered to improve landmark detection
# Map dataset folder names to gesture labels
GESTURE_MAPPING = {
    '0': 'wave', '1': 'stop', '2': 'thumbs_up',
    'wave': 'wave', 'stop': 'stop', 'thumbs_up': 'thumbs_up'
}
GESTURE_LABELS = {0: 'wave', 1: 'stop', 2: 'thumbs_up'}

# ====== MEDIAPIPE SETUP ======
mp_hands = mp.solutions.hands
mp_drawing = mp.solutions.drawing_utils
hands = mp_hands.Hands(max_num_hands=1, min_detection_confidence=MIN_DETECTION_CONFIDENCE)

def extract_features(landmarks):
    """Extract 3D coordinates from hand landmarks."""
    if not landmarks:
        return np.zeros(21 * 3)
    return np.array([coord for lm in landmarks for coord in (lm.x, lm.y, lm.z)])

def augment_image(image):
    """Apply random rotation, flip, and brightness adjustment for data augmentation."""
    angle = np.random.uniform(-15, 15)
    h, w = image.shape[:2]
    M = cv2.getRotationMatrix2D((w/2, h/2), angle, 1)
    rotated = cv2.warpAffine(image, M, (w, h))
    if np.random.rand() > 0.5:
        rotated = cv2.flip(rotated, 1)
    # Adjust brightness
    brightness = np.random.uniform(0.8, 1.2)
    rotated = np.clip(rotated * brightness, 0, 255).astype(np.uint8)
    return rotated

def download_kagglehub_dataset():
    """Download and process Kaggle dataset with strict class filtering."""
    print("⏳ Downloading dataset from KaggleHub...")
    try:
        path = kagglehub.dataset_download(KAGGLE_DATASET)
        print("✅ Dataset downloaded to:", path)
    except Exception as e:
        print(f"❌ Failed to download dataset: {e}")
        path = "./gesture-recognition-dataset"  # Adjust to local path
        if not os.path.exists(path):
            print("❌ Dataset path not found. Download from https://www.kaggle.com/datasets/abhishek14398/gesture-recognition-dataset")
            return None, None

    # Find directories with images
    image_dirs = []
    for root, dirs, files in os.walk(path):
        for dir_name in dirs:
            dir_path = os.path.join(root, dir_name)
            image_files = [f for f in os.listdir(dir_path) if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
            if image_files:
                image_dirs.append(dir_path)

    if not image_dirs:
        print("❌ No folders with images found.")
        return None, None

    # Filter directories to only valid gestures
    valid_dirs = []
    for dir_path in image_dirs:
        folder_name = os.path.basename(dir_path).lower()
        if folder_name in GESTURE_MAPPING:
            valid_dirs.append((dir_path, GESTURE_MAPPING[folder_name]))
    print(f"📂 Valid gesture folders: {[f[0] for f in valid_dirs]}")

    if not valid_dirs:
        print("❌ No valid gesture folders found. Expected: wave, stop, thumbs_up or 0, 1, 2.")
        return None, None

    X, y = [], []
    for class_id, gesture in enumerate(GESTURE_LABELS.values()):
        matching_dirs = [d[0] for d in valid_dirs if d[1] == gesture]
        for folder in matching_dirs:
            print(f"📂 Processing folder: {os.path.basename(folder)} (Class ID: {class_id})")
            image_paths = glob.glob(os.path.join(folder, "*.*"))[:MAX_IMAGES_PER_CLASS]
            if not image_paths:
                print(f"⚠️ No images found in {folder}")
                continue
            print(f"📁 Found {len(image_paths)} images")

            for image_path in tqdm(image_paths, desc=f"Processing {gesture}"):
                img = cv2.imread(image_path)
                if img is None:
                    print(f"❌ Failed to read: {image_path}")
                    continue
                img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
                for _ in range(AUGMENTATION_FACTOR):
                    aug_img = augment_image(img_rgb) if _ > 0 else img_rgb
                    result = hands.process(aug_img)
                    if result.multi_hand_landmarks:
                        for hand_landmarks in result.multi_hand_landmarks:
                            feature = extract_features(hand_landmarks.landmark)
                            X.append(feature)
                            y.append(class_id)
                    else:
                        print(f"⚠️ No hand landmarks detected in {image_path}")

    X, y = np.array(X), np.array(y)
    if len(X) == 0:
        print("❌ No valid data extracted. Check dataset images or MediaPipe detection.")
        return None, None

    print(f"✅ Extracted {len(X)} samples with {len(np.unique(y))} classes")
    np.savez(DATA_PATH, X=X, y=y)
    print(f"✅ Saved dataset to {DATA_PATH}")
    return X, y

def setup_live_plot():
    """Initialize live plot for gesture confidence."""
    plt.ion()
    fig, ax = plt.subplots(figsize=(8, 4))
    scores = deque(maxlen=30)
    line, = ax.plot(scores, color='#1f77b4')
    ax.set_ylim(0, 1)
    ax.set_title("Real-Time Gesture Confidence")
    ax.set_xlabel("Frames")
    ax.set_ylabel("Confidence")
    ax.grid(True)
    return fig, ax, line, scores

def train_and_run():
    """Train the model and run real-time inference with webcam."""
    # Load or process data
    if os.path.exists(DATA_PATH):
        try:
            with np.load(DATA_PATH) as data:
                X, y = data['X'], data['y']
                print(f"✅ Loaded dataset from {DATA_PATH}: {len(X)} samples, {len(np.unique(y))} classes")
        except Exception as e:
            print(f"❌ Failed to load dataset: {e}")
            X, y = None, None
    else:
        X, y = download_kagglehub_dataset()

    if X is None or y is None or len(X) == 0:
        print("⛔ No valid data available. Exiting.")
        return

    # Train model with feature scaling
    try:
        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
        scaler = StandardScaler()
        X_train = scaler.fit_transform(X_train)
        X_test = scaler.transform(X_test)
        classifier = RandomForestClassifier(n_estimators=100, random_state=42)
        classifier.fit(X_train, y_train)
        print(f"✅ Model trained. Test Accuracy: {accuracy_score(y_test, classifier.predict(X_test)):.2f}")
    except Exception as e:
        print(f"❌ Failed to train model: {e}")
        return

    # Real-time inference with webcam
    cap = cv2.VideoCapture(0)
    if not cap.isOpened():
        print("❌ Failed to open webcam. Exiting.")
        return
    fig, ax, line, scores = setup_live_plot()

    try:
        while True:
            ret, frame = cap.read()
            if not ret:
                print("❌ Failed to capture frame.")
                break
            rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            results = hands.process(rgb)

            if results.multi_hand_landmarks:
                for hand_landmarks in results.multi_hand_landmarks:
                    mp_drawing.draw_landmarks(frame, hand_landmarks, mp_hands.HAND_CONNECTIONS)
                    features = extract_features(hand_landmarks.landmark).reshape(1, -1)
                    features = scaler.transform(features)  # Apply scaling to inference features
                    probs = classifier.predict_proba(features)[0]
                    gesture_idx = np.argmax(probs)
                    gesture_name = GESTURE_LABELS.get(gesture_idx, "Unknown")
                    confidence = probs[gesture_idx]

                    scores.append(confidence)
                    line.set_ydata(scores)
                    line.set_xdata(np.arange(len(scores)))
                    ax.relim()
                    ax.autoscale_view()
                    fig.canvas.draw()
                    fig.canvas.flush_events()

                    cv2.putText(frame, f"{gesture_name} ({confidence:.2f})", (10, 30),
                                cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2)

            cv2.imshow("Real-Time Gesture Recognition", frame)
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
    finally:
        cap.release()
        cv2.destroyAllWindows()
        plt.close()

if __name__ == "__main__":
    train_and_run()

✅ Loaded dataset from gesture_data.npz: 28180 samples, 755 classes
✅ Model trained. Test Accuracy: 0.68
❌ Failed to open webcam. Exiting.
